In [1]:
import pandas as pd
from IPython.display import clear_output, Markdown, Math
import ipywidgets as widgets
import os
import unicodedata as uni
import numpy as np
from nltk.stem import PorterStemmer
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.corpus import wordnet
import math
import pprint

pp=pprint.PrettyPrinter(indent=4)

# Naive Approach

* read in table

In [2]:
table = pd.read_csv('../Tools/emoji_descriptions.csv')
table.head()

Unnamed: 0    code character               description  \
0           0  126980         🀄   MAHJONG TILE RED DRAGON   
1           1  129525         🧵           SPOOL OF THREAD   
2           2  129526         🧶              BALL OF YARN   
3           3  127183         🃏  PLAYING CARD BLACK JOKER   
4           4  129296         🤐         ZIPPER-MOUTH FACE   

              description_de  
0  MAHJONG FLIESE ROT DRACHE  
1              Spool Gewinde  
2               BALL OF YARN  
3     SPIELKARTE BLACK JOKER  
4        ZIPPER-MUND Gesicht

* todo: read in a lot of messages

In [3]:
messages = ["Hello, this is a testing message", "this is a very sunny day today, i am very happy"]

* using a Stemmer to get the main 'Part' of each word

In [4]:
ps = PorterStemmer()

In [5]:
stemmed_messages = []
for m in messages:
    words = word_tokenize(m)
    sm = []
    for w in words:
        sm.append(ps.stem(w))
    stemmed_messages.append(sm)

In [6]:
stemmed_messages

[['hello', ',', 'thi', 'is', 'a', 'test', 'messag'],
 ['thi',
  'is',
  'a',
  'veri',
  'sunni',
  'day',
  'today',
  ',',
  'i',
  'am',
  'veri',
  'happi']]

In [7]:
table.shape

(1027, 5)

* compare words to emoji descriptions

In [8]:
def evaluate_sentence(sentence, description_key = 'description'):
    tokenized_sentence = word_tokenize(sentence)
    n = len(tokenized_sentence)
    l = table.shape[0]
    matrix_list = []
    
    for index, row in table.iterrows():
        emoji_tokens = word_tokenize(row[description_key])
        m = len(emoji_tokens)

        mat = np.zeros(shape=(m,n))
        for i in range(len(emoji_tokens)):
            for j in range(len(tokenized_sentence)):
                syn1 = wordnet.synsets(emoji_tokens[i])
                if len(syn1) == 0:
                    continue
                w1 = syn1[0]
                #print(j, tokenized_sentence)
                syn2 = wordnet.synsets(tokenized_sentence[j])
                if len(syn2) == 0:
                    continue
                w2 = syn2[0]
                val = w1.wup_similarity(w2)
                if val is None:
                    continue
                mat[i,j] = val
        #print(row['character'], mat)
        matrix_list.append(mat)
            
    return matrix_list
    
    

* building a lookup table:

In [9]:
lookup = {}
emoji_set = []
for index, row in table.iterrows():
    lookup[index] = row['character']
    emoji_set.append(row['character'])

emoji_set = set(emoji_set)

* sorting

In [10]:
def predict(sentence, description_key='description', n=10, t=0.9):

    result = evaluate_sentence(sentence, description_key)
    
    summed = np.argsort([-np.sum(x) for x in result])[0:n]
    max_val = np.argsort([-np.max(x) for x in result])[0:n]
    avg =  np.argsort([-np.mean(x) for x in result])[0:n]
    threshold = np.argsort([-len(np.where(x>t)[0]) / (x.shape[0] * x.shape[1]) for x in result])[0:n]
    
    # build a result table
    table_array = [[lookup[summed[i]], str(table.iloc[summed[i]][description_key]), 
                    lookup[max_val[i]], str(table.iloc[max_val[i]][description_key]),
                    lookup[avg[i]], str(table.iloc[avg[i]][description_key]),
                    lookup[threshold[i]], str(table.iloc[threshold[i]][description_key])] for i in range(n) ]
    
    
    table_frame = pd.DataFrame(table_array, columns=['summed', 'summed_description','max_val', 'max_val_description','avg', 'avg_description','threshold', 'threshold_description'])
    
    display(table_frame)


In [11]:
predict("I love sunny days!", description_key='description' )

summed                                 summed_description max_val  \
0      🤪     GRINNING FACE WITH ONE LARGE AND ONE SMALL EYE       🤟   
1      🚮                     PUT LITTER IN ITS PLACE SYMBOL       💌   
2      🖖  RAISED HAND WITH PART BETWEEN MIDDLE AND RING ...       🇮   
3      🥰    SMILING FACE WITH SMILING EYES AND THREE HEARTS       🏩   
4      🤭  SMILING FACE WITH SMILING EYES AND HAND COVERI...       😱   
5      🔂  CLOCKWISE RIGHTWARDS AND LEFTWARDS OPEN CIRCLE...       🇭   
6      🔛  ON WITH EXCLAMATION MARK WITH LEFT RIGHT ARROW...       🇳   
7      🔠             INPUT SYMBOL FOR LATIN CAPITAL LETTERS       🇴   
8      🤟                               I LOVE YOU HAND SIGN       📲   
9      🇮                 REGIONAL INDICATOR SYMBOL LETTER I       🌆   

                          max_val_description avg  avg_description threshold  \
0                        I LOVE YOU HAND SIGN   💢     ANGER SYMBOL         💌   
1                                 LOVE LETTER   📦          PACKAGE         🏩   
2          REGIONAL INDICATOR SYMBOL LETTER I   💌      LOVE LETTER         🤟   
3                                  LOVE HOTEL   🆑       SQUARED CL         🇮   
4                      FACE SCREAMING IN FEAR   🌉  BRIDGE AT NIGHT         📨   
5          REGIONAL INDICATOR SYMBOL LETTER H   💐          BOUQUET         📩   
6          REGIONAL INDICATOR SYMBOL LETTER N   📜           SCROLL         📪   
7          REGIONAL INDICATOR SYMBOL LETTER O   🎁  WRAPPED PRESENT         📫   
8  MOBILE PHONE WITH RIGHTWARDS ARROW AT LEFT   💨      DASH SYMBOL         📰   
9                           CITYSCAPE AT DUSK   💤  SLEEPING SYMBOL         📬   

                 threshold_description  
0                          LOVE LETTER  
1                           LOVE HOTEL  
2                 I LOVE YOU HAND SIGN  
3   REGIONAL INDICATOR SYMBOL LETTER I  
4                    INCOMING ENVELOPE  
5  ENVELOPE WITH DOWNWARDS ARROW ABOVE  
6     CLOSED MAILBOX WITH LOWERED FLAG  
7      CLOSED MAILBOX WITH RAISED FLAG  
8                            NEWSPAPER  
9        OPEN MAILBOX WITH RAISED FLAG